# EDA of STEM SALARIES

This is an Exploration Data Analysis of Data Science and STEM Salaries taken from https://www.kaggle.com/code/febiec/data-science-and-tech-salaries-visualization/data. Based on this notebook it is taken from various industry from June 2017 to August 2021

### Table of Contents


Load the data and necessary packages

In [2]:
import pandas as pd
import csv
import matplotlib.pyplot as plt
plt.style.use('ggplot')
plt.rcParams["figure.figsize"] = (12, 18)
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', 1000)

#Reference1
#https://towardsdatascience.com/a-beginners-guide-to-grabbing-and-analyzing-salary-data-in-python-e8c60eab186e

#Reference2
#https://www.kaggle.com/code/febiec/data-science-and-tech-salaries-visualization/notebook

# Python ≥3.5 is required
import sys
assert sys.version_info >= (3, 5)

# Scikit-Learn ≥0.20 is required
import sklearn
assert sklearn.__version__ >= "0.20"

# Common imports
import numpy as np
import os

# To plot pretty figures
%matplotlib inline
import matplotlib as mpl
import matplotlib.pyplot as plt
mpl.rc('axes', labelsize=14)
mpl.rc('xtick', labelsize=12)
mpl.rc('ytick', labelsize=12)

# Where to save the figures
PROJECT_ROOT_DIR = "."
CHAPTER_ID = "end_to_end_project"
IMAGES_PATH = os.path.join(PROJECT_ROOT_DIR, "images", CHAPTER_ID)
os.makedirs(IMAGES_PATH, exist_ok=True)

def save_fig(fig_id, tight_layout=True, fig_extension="png", resolution=300):
    path = os.path.join(IMAGES_PATH, fig_id + "." + fig_extension)
    print("Saving figure", fig_id)
    if tight_layout:
        plt.tight_layout()
    plt.savefig(path, format=fig_extension, dpi=resolution)

ModuleNotFoundError: No module named 'matplotlib'

In [ ]:
filepath = "/Users/hafidpradipta/PythonTraining/KaggleTraining/Data Science Tech Visualization/Levels_Fyi_Salary_Data.csv"
stem_salaries = pd.read_csv(filepath)
stem_salaries.shape

(62642, 29)

## Data Sanity

This dataset has 29 columns. I will skim the dataset and make decision on which columns that I want to retain. I don't want to analyze based on gender and race. So I will throw them. I will also throw some column about on hot encoding in education as the last column already tells the education level. I will pick the following 12 columns. 

Note: on the colum "Otherdetails" there are valuable information such as "+ $12.5k signing, Post-IPO offer. New ESPP could add 4k - 20k to TC, Title: Software Engineer 1, Academic Level: Bachelor’s degree". I found it too complicated to analyze so I will drop this column. It will impact the 'totalyearlycompensation' and I will figure out how to make the calculation simpler. 


In [ ]:
ssdf = stem_salaries[['company', 'level', 'title', 'totalyearlycompensation',
       'location', 'yearsofexperience', 'yearsatcompany', 'tag', 'basesalary',
       'stockgrantvalue', 'bonus','Education']]

In [ ]:
#based on reference 2,I also want to remove some of the unrelated titles 
#Marketing, Mechanical Engineer, Sales, Recruiter, Human Resources.
ssdf.title.value_counts()

Software Engineer               41231
Product Manager                  4673
Software Engineering Manager     3569
Data Scientist                   2578
Hardware Engineer                2200
Product Designer                 1516
Technical Program Manager        1381
Solution Architect               1157
Management Consultant             976
Business Analyst                  885
Marketing                         710
Mechanical Engineer               490
Sales                             461
Recruiter                         451
Human Resources                   364
Name: title, dtype: int64

I basically start the analysis using pandas_profiling and here are several decision that I made: 
- Some level and company are missing. I don't want my dataset to have missing data on these columns
- Some company's name are similar to each other so I convert the company's name into lower case
- Some of the base salary is 0. I don't want to analyze charity. I am analyzing a business. so I removed it. 


In [ ]:

'''from pandas_profiling import ProfileReport
profile = ProfileReport(ssdf, title = "Stem Salaries")
profile.to_notebook_iframe()'''

'from pandas_profiling import ProfileReport\nprofile = ProfileReport(ssdf, title = "Stem Salaries")\nprofile.to_notebook_iframe()'

I make a function to see what are the full values in a given column and here are my finding: 
- There are typo in the company name such as Amazon and amazn. I can't afford to look it one by one so I let it as is. 
- it seems that most of the survey are from top big companies such as Amazon, Microsoft, Google, etc. So I create a column 'companysize' refering to the company size *in this survey*. Small for < 100 respondent, medium for 100 - 1000 and big for 1000++ respondents. 


In [ ]:
def groupDescriptive(data, columns):
    temp1 = data.groupby(columns, as_index = False).size()
    temp1 = pd.DataFrame(temp1)
    temp1.columns = [columns,'count']
    temp1 = temp1.sort_values(by = ['count'],ascending= False)
    temp1.to_csv("temp1", sep=',')
    return temp1

In [ ]:
lvlTemp = groupDescriptive(ssdf, 'company')
lvlTemp.sort_values(by =['count'], ascending = False)

company  count
64         Amazon   8126
818     Microsoft   5216
556        Google   4330
461      Facebook   2990
95          Apple   2028
...           ...    ...
1478  homeadvisor      1
1479        houzz      1
1487       idemia      1
1490     infinera      1
1630       Google      1

[1631 rows x 2 columns]

There are small amount of respondent who has been 25+ years at the company. I don't want to analzye them because I am not going to prepare my life for the next 25 years. I looked at their yearly compensation. Some of them earn one million USD and the rest at around 250k. I don't they worth my analysis. It's too far ahead. I may open a chicken farm in 25 years. 

There are 97 respondents who has > 30 years of experience. They have gone a long way from dial up internet to right now. I think they are too distant from my main analysis. I will exclude them. 


In [ ]:
yacTemp = groupDescriptive(ssdf, 'yearsatcompany')
yacTemp.sort_values(by =['yearsatcompany'], ascending = False).head(20)

yearsatcompany  count
80            69.0      1
79            40.0      1
78            34.0      2
77            33.0      2
76            32.0      1
75            30.0      2
74            28.0      2
73            27.0      5
72            26.0      6
71            25.0     23
70            24.0     12
69            23.0     20
68            22.0     25
67            21.0     30
66            20.0    168
65            19.0     53
64            18.0     60
63            17.0     54
62            16.0     98
61            15.5      1

In [ ]:
ssdf[ssdf['yearsofexperience'] > 30].shape

(97, 12)

In [ ]:
ssdf[ssdf['yearsatcompany'] > 25].shape

(22, 12)

When I look at the column 'location' for those who are from the US only has 2 information, City Name, and state code. For those who are outside of the US, they have 3 informations, City Name, State Code and Country.  I will split these columns into three columns

In [ ]:
groupDescriptive(ssdf,'location')

location  count
858          Seattle, WA   8701
822    San Francisco, CA   6797
644         New York, NY   4562
765          Redmond, WA   2649
609    Mountain View, CA   2275
..                   ...    ...
346       Glen Allen, VA      1
348  Gliwice, SL, Poland      1
349       Goa, GA, India      1
771       Reidsville, NC      1
583          Miramar, FL      1

[1050 rows x 2 columns]

In [ ]:
ssdf['tycCat']  = pd.cut(ssdf['totalyearlycompensation'],
                                    bins=[0, 1000000, 2000000, 3000000, 4000000,  np.inf],
                                    labels=['0-1M','1-2M','2-3M','3-4M','4M++'])

/var/folders/pb/wv0xyth936z960_d27b10g2h0000gn/T/ipykernel_25642/4081997038.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  ssdf['tycCat']  = pd.cut(ssdf['totalyearlycompensation'],


In [ ]:
tycCatTemp = groupDescriptive(ssdf,'tycCat')
tycCatTemp

tycCat  count
0   0-1M  62532
1   1-2M    103
4   4M++      4
2   2-3M      3
3   3-4M      0

Most of the millionaire(respondents who earns more than 1M USD) have 10+ years experience at the top company. I want to exclude them because I am happy earning 90K per year. Meaning that, I would consider this an outlier because the years of experience is too far and they are too stellar. Credit for them but not for this analysis. 

In [ ]:
millabove = ssdf[ssdf['totalyearlycompensation'] >= 1000000]
millabovetemp = millabove[['company', 'yearsofexperience', 'level']].groupby([ 'yearsofexperience', 'company','level']).size()
temp1= millabovetemp
temp1.to_csv("temp1", sep=',')


I want to see people who earn more than 750k. I got a hunch that their salaries are in the range of 250K but they have 500k worth of stock. I will investigate later. 

In [ ]:
sfk = ssdf[(ssdf['totalyearlycompensation'] <= 1000000) & (ssdf['totalyearlycompensation'] >= 750000)]
temp1= sfk
temp1.to_csv("temp1", sep=',')

### Data Cleaning

In [ ]:
def data_cleaning(ssdf):

    #select only related columns

    ssdf = ssdf[['timestamp','company', 'level', 'title', 'totalyearlycompensation',
       'location', 'yearsofexperience', 'yearsatcompany', 'tag', 'basesalary',
       'stockgrantvalue', 'bonus','Education']]

    #1 replace empty value with NaN
    ssdf = ssdf.replace("", np.nan)

    # change the timestamp into datetime
    ssdf['timestamp'] = pd.to_datetime(ssdf['timestamp'])

    #make sure all numeric columns are numeric
    ssdf[['yearsofexperience','basesalary','bonus','stockgrantvalue','totalyearlycompensation','yearsatcompany']] = ssdf[['yearsofexperience','basesalary','bonus','stockgrantvalue','totalyearlycompensation','yearsatcompany']].apply(pd.to_numeric)

    # removes uncessary title
    undesired_titles = ['Marketing', 'Mechanical Engineer', 'Sales', 'Recruiter', 'Human Resources']
    ssdf = ssdf[ssdf['title'].apply(lambda x: x not in undesired_titles)]

   # I don't care when soemone has no level and has no company's name
    ssdf = ssdf.dropna(how = 'any', subset = ['level', 'company'])
    
    #
    ssdf['company'] = ssdf['company'].str.lower()
    lvlTemp = groupDescriptive(ssdf, 'company')
    #how to clean duplicates name
    lvlTemp.sort_values(by =['company'])
    lvlTemp['companysize'] = pd.cut(lvlTemp['count'],
                                    bins=[0, 100, 1000,  np.inf],
                                    labels=['small','med','big'])
    lvlTempIdx = lvlTemp[['company', 'companysize']]
    ssdf = ssdf.merge(lvlTempIdx, on= 'company', how = 'left')
    
   #3  I don't care when someone works more than I lived
    ssdf = ssdf[ssdf['yearsofexperience'] <= 30]
    # I may not be loyal to a company so I limit the years at company to 25 
    ssdf = ssdf[ssdf['yearsatcompany'] <= 25] 

   # I don't like to dream big. I am happy if I can earn 6 digits. So I will remove the millionaire.  
    ssdf = ssdf[ssdf['totalyearlycompensation'] < 1000000]

   #4 convert company's name to lower case
    ssdf['company'] = ssdf['company'].str.lower()

    #5 I don't want a datapoint that has no salary
    ssdf = ssdf[ssdf['basesalary'] != 0]

    # Later on I want to do geographical analysis. So I will split the location into three separate columns
    ssdf[['CityName','StateCode','Country','Country2']] = ssdf['location'].str.split(',', expand = True)
    ssdf['Country'] = ssdf['Country'].replace({None:'US'})
    ssdf = ssdf.drop(columns = ['Country2'])

    #write to csv so I can better eyeball it
    temp1 = ssdf
    temp1.to_csv("temp1", sep=',')

    return ssdf

    

In [ ]:
ssdfClean = data_cleaning(stem_salaries)

In [ ]:
ssdfClean

timestamp     company     level                         title  \
0     2017-06-07 11:33:27      oracle        L3               Product Manager   
2     2017-06-11 14:53:57      amazon        L7               Product Manager   
3     2017-06-17 00:23:14       apple        M1  Software Engineering Manager   
6     2017-06-22 12:37:51   microsoft        65  Software Engineering Manager   
7     2017-06-22 13:55:26   microsoft        62             Software Engineer   
...                   ...         ...       ...                           ...   
60051 2018-09-09 11:52:32      google        T4             Software Engineer   
60052 2018-09-13 08:23:32   microsoft        62             Software Engineer   
60053 2018-09-13 14:35:59        msft        63             Software Engineer   
60054 2018-09-16 16:10:35  salesforce  Lead MTS             Software Engineer   
60055 2019-01-29 05:12:59       apple      ict3             Software Engineer   

       totalyearlycompensation           location  yearsofexperience  \
0                       127000   Redwood City, CA                1.5   
2                       310000        Seattle, WA                8.0   
3                       372000      Sunnyvale, CA                7.0   
6                       300000        Redmond, WA               15.0   
7                       156000        Seattle, WA                4.0   
...                        ...                ...                ...   
60051                   327000        Seattle, WA               10.0   
60052                   237000        Redmond, WA                2.0   
60053                   220000        Seattle, WA               14.0   
60054                   280000  San Francisco, CA                8.0   
60055                   200000      Sunnyvale, CA                0.0   

       yearsatcompany                             tag  basesalary  \
0                 1.5                             NaN    107000.0   
2                 0.0                             NaN    155000.0   
3                 5.0                             NaN    157000.0   
6                11.0                             NaN    180000.0   
7                 4.0                             NaN    135000.0   
...               ...                             ...         ...   
60051             1.0  Distributed Systems (Back-End)    155000.0   
60052             2.0                      Full Stack    146900.0   
60053            12.0                      Full Stack    157000.0   
60054             4.0                             iOS    194688.0   
60055             0.0                         ML / AI    155000.0   

       stockgrantvalue    bonus Education companysize       CityName  \
0              20000.0  10000.0       NaN         big   Redwood City   
2                  0.0      0.0       NaN         big        Seattle   
3             180000.0  35000.0       NaN         big      Sunnyvale   
6              65000.0  55000.0       NaN         big        Redmond   
7               8000.0  13000.0       NaN         big        Seattle   
...                ...      ...       ...         ...            ...   
60051         150000.0  22000.0       NaN         big        Seattle   
60052          73200.0  16000.0       NaN         big        Redmond   
60053          25000.0  20000.0       NaN       small        Seattle   
60054          57000.0  29000.0       NaN         big  San Francisco   
60055          27000.0  19000.0       NaN         big      Sunnyvale   

      StateCode Country  
0            CA      US  
2            WA      US  
3            CA      US  
6            WA      US  
7            WA      US  
...         ...     ...  
60051        WA      US  
60052        WA      US  
60053        WA      US  
60054        CA      US  
60055        CA      US  

[57557 rows x 17 columns]

In [ ]:
from pandas_profiling import ProfileReport
profile = ProfileReport(ssdfClean, title = "Stem Salaries")
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

The second analysis
